# In-Class Assignment: Text Similarity \& Recommendation Systems

## *IS 5150*
## Name: Key

In this in-class assignment we will utilize two different distance metrics to measure the similarity between movie descriptions in order to create a movie recommender. We will utilize content-based filtering in order to find movies with similar plot descriptions so that we can then recommend like movies. Ideally we would use more than just plot description, but you might be surprised to see how good recommendations can be using plot descriptions alone!

The two distance metrics we will be examining include:
1. Cosine Similarity
2. Okapi BM25 ranking

The dataset we will be working with can be pulled from Kaggle [here](https://www.kaggle.com/datasets/tmdb/tmdb-movie-metadata), which contains metadata of 5,000 movies from The Movie Database (TMDB), an open-source, editable database for movies and TV shows.

Let's bring in the `tmdb_5000_movies.csv` file and take a look at its contents, as well as load our necessary dependencies.

In [ ]:
import pandas as pd
import nltk
import re
import numpy as np

nltk.download()
'punkt'

from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity

In [ ]:
df = pd.read_csv('tmdb_5000_movies.csv')
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4803 entries, 0 to 4802
Data columns (total 20 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   budget                4803 non-null   int64  
 1   genres                4803 non-null   object 
 2   homepage              1712 non-null   object 
 3   id                    4803 non-null   int64  
 4   keywords              4803 non-null   object 
 5   original_language     4803 non-null   object 
 6   original_title        4803 non-null   object 
 7   overview              4800 non-null   object 
 8   popularity            4803 non-null   float64
 9   production_companies  4803 non-null   object 
 10  production_countries  4803 non-null   object 
 11  release_date          4802 non-null   object 
 12  revenue               4803 non-null   int64  
 13  runtime               4801 non-null   float64
 14  spoken_languages      4803 non-null   object 
 15  status               

**Amongst our columns of interest `genres`, `tagline`, `overview` and `title` do we have missing data?**

Yes, there is missing data for overview and tagline.

## Building a Movie Recommender System

We will take the following steps to build the recommender system:

1) Prep the dataframe


2) Preprocess the text


3) Feature Engineering


4) Document Similairty Computation


5) Find top similar movies


6) Create a movie recommender function

### 1) Prep the Dataframe

Let's take a few data preparation steps, including dropping out unneccesary columns (we just care about text columns in this case), getting rid of null values, and merging the `tagline` column with the `overview` column as a plot `description` column.

In [ ]:
df = df[['title', 'tagline', 'overview', 'genres', 'popularity']] # subset the original df down to just the variables of internet
df.tagline.fillna('', inplace=True)                               # find blank taglines and fill with with nan values
df['description'] = df['tagline'].map(str) + ' ' + df['overview'] # create a new description column by combining tagline with overview
df.dropna(inplace=True)                                           # remove rows with missing data from df
df.info()                                                         # pulling up the df information

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4800 entries, 0 to 4802
Data columns (total 6 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   title        4800 non-null   object 
 1   tagline      4800 non-null   object 
 2   overview     4800 non-null   object 
 3   genres       4800 non-null   object 
 4   popularity   4800 non-null   float64
 5   description  4800 non-null   object 
dtypes: float64(1), object(5)
memory usage: 262.5+ KB


In [ ]:
df.head()

title  \
0                                    Avatar   
1  Pirates of the Caribbean: At World's End   
2                                   Spectre   
3                     The Dark Knight Rises   
4                               John Carter   

                                          tagline  \
0                     Enter the World of Pandora.   
1  At the end of the world, the adventure begins.   
2                           A Plan No One Escapes   
3                                 The Legend Ends   
4            Lost in our world, found in another.   

                                            overview  \
0  In the 22nd century, a paraplegic Marine is di...   
1  Captain Barbossa, long believed to be dead, ha...   
2  A cryptic message from Bond’s past sends him o...   
3  Following the death of District Attorney Harve...   
4  John Carter is a war-weary, former military ca...   

                                              genres  popularity  \
0  [{"id": 28, "name": "Action"}, {"id": 12, "nam...  150.437577   
1  [{"id": 12, "name": "Adventure"}, {"id": 14, "...  139.082615   
2  [{"id": 28, "name": "Action"}, {"id": 12, "nam...  107.376788   
3  [{"id": 28, "name": "Action"}, {"id": 80, "nam...  112.312950   
4  [{"id": 28, "name": "Action"}, {"id": 12, "nam...   43.926995   

                                         description  
0  Enter the World of Pandora. In the 22nd centur...  
1  At the end of the world, the adventure begins....  
2  A Plan No One Escapes A cryptic message from B...  
3  The Legend Ends Following the death of Distric...  
4  Lost in our world, found in another. John Cart...

### 2) Preprocess the Text

In this next step we will define a normalize document function since this isn't particulary complicated text. Let's think about what steps we need to take in cleaning and normalization, and which we don't.

In [ ]:
stop_words = nltk.corpus.stopwords.words('english')

def normalize_document(doc):
    doc = re.sub(r'[^a-zA-Z0-9\s]', '', doc, re.I|re.A)           # lower case and remove special characters\whitespaces
    doc = doc.lower()
    doc = doc.strip()
    tokens = nltk.word_tokenize(doc)                              # tokenize document
    filtered_tokens = [token for token in tokens if token not in stop_words]
    doc = ' '.join(filtered_tokens)                               # filter stopwords out of document, then rejoin document
    return doc

normalize_corpus = np.vectorize(normalize_document)

norm_corpus = normalize_corpus(list(df['description']))
len(norm_corpus)

4800

In [ ]:
norm_corpus[0:5]

array(['enter world pandora 22nd century paraplegic marine dispatched moon pandora unique mission becomes torn following orders protecting alien civilization',
       'end world adventure begins captain barbossa long believed dead come back life headed edge earth turner elizabeth swann nothing quite seems',
       'plan one escapes cryptic message bonds past sends trail uncover sinister organization battles political forces keep secret service alive bond peels back layers deceit reveal terrible truth behind spectre',
       'legend ends following death district attorney harvey dent batman assumes responsibility dents crimes protect late attorneys reputation subsequently hunted gotham city police department eight years later batman encounters mysterious selina kyle villainous bane new terrorist leader overwhelms gothams finest dark knight resurfaces protect city branded enemy',
       'lost world found another john carter warweary former military captain whos inexplicably transported my

### 3) Feature Engineering - Extract TF-IDF Features

For this task we will use TFIDF features, and will utilize the `TfidfVectorizer` from `sklearn`.

In [ ]:
tf = TfidfVectorizer(ngram_range=(1, 2), min_df=2)     # set parameters for tf-idf for unigrams and bigrams
tfidf_matrix = tf.fit_transform(norm_corpus)           # extract tfidf features from norm_corpus
tfidf_matrix.shape                                      

(4800, 20667)

**What do these two values tell refer to?**

We have 4,800 documents and 20667 TF-IDF features making a 4800x20667 matrix

### 4a) Compute Pairwise Document Similarity - Cosine Similarity

We'll run through calculating document similarity first with cosine similarity, then we'll repeat the process with our second distance metric.

In [ ]:
doc_sim = cosine_similarity(tfidf_matrix)                      # compute document similarity by examining the cosine similairty b/w documents in matrix
doc_sim_df = pd.DataFrame(doc_sim)                             # take doc_sim, convert to dataframe
doc_sim_head = doc_sim_df.head()                               # pull up a heading of the dataframe 
doc_sim_head.style.background_gradient(cmap="Blues")           # apply a background gradient to highlight stronger similarity

### 5a) Find Top Similar Movies for a Sample Movie

Our next step will be getting the list of movies from our `df['title']` column, and then examining the top most similar movies for a sample movie choice. Let's see what comes up for the movie *Interstellar* (or you can choose a different one).

We'll take the following steps:
* Create a list of our movie titles
* Locate our sample movie's index number
* Save movie similarity values
* Extract the top 5 most similar to our sample movie
* Print out their names

In [ ]:
movie_list = df['title'].values                                             # saving all the unique movie titles to a list
movie_list

array(['Avatar', "Pirates of the Caribbean: At World's End", 'Spectre',
       ..., 'Signed, Sealed, Delivered', 'Shanghai Calling',
       'My Date with Drew'], dtype=object)

In [ ]:
movie_idx = np.where(movie_list == 'Interstellar')[0][0]                   # extracted the index number for the sample movie
movie_idx

95

In [ ]:
movie_similarities = doc_sim_df.iloc[movie_idx].values                     # extracting the similarity scores associated with the sample movie
movie_similarities

array([0.        , 0.01778893, 0.        , ..., 0.        , 0.        ,
       0.        ])

In [ ]:
similar_movie_idxs = np.argsort(-movie_similarities)[1:6]                 # save the movie index of the top 5 highest similarity scores
similar_movies = movie_list[similar_movie_idxs]                           # pull out the movie names associated with those top 5 movie indices
similar_movies

array(['Gattaca', 'Space Pirate Captain Harlock', 'Space Cowboys',
       'Starship Troopers', 'Final Destination 2'], dtype=object)

In [ ]:
df['overview'].loc[95]

'Interstellar chronicles the adventures of a group of explorers who make use of a newly discovered wormhole to surpass the limitations on human space travel and conquer the vast distances involved in an interstellar voyage.'

In [ ]:
np.where(movie_list == 'Final Destination 2')[0][0]
df['overview'].loc[1789]

"When Kimberly has a violent premonition of a highway pileup she blocks the freeway, keeping a few others meant to die, safe...Or are they? The survivors mysteriously start dying and it's up to Kimberly to stop it before she's next."

**How did the movie recommender perform? Are the suggestions logical, are some of them more illogical? Of the recommendations that do make sense, what overlap might be being captured between these movies?**

### 6a) Build a movie recommender function

Now let's define a function to recommend the top 5 similar movies for any movie in our dataset:

In [ ]:
def movie_recommender(movie_title, movies=movie_list, doc_sims=doc_sim_df):
    # find movie id
    movie_idx = np.where(movies == movie_title)[0][0]
    # get movie similarities
    movie_similarities = doc_sims.iloc[movie_idx].values
    # get top 5 similar movie IDs
    similar_movie_idxs = np.argsort(-movie_similarities)[1:6]
    # get top 5 movies
    similar_movies = movies[similar_movie_idxs]
    # return the top 5 movies
    return print("Based on your interest in", movie_title,"I'd Recommend checking out:", similar_movies)

In [ ]:
movie_recommender('Dune')

Based on your interest in Dune I'd Recommend checking out: ['Epic' 'Krull' 'Million Dollar Baby' 'Warriors of Virtue' 'Listening']


**Have a friend/family member/partner try out your movie recommender and report how it performs on their selected movie! Did they find a new movie they'd consider watching?**

### 4b) Compute Pairwise Document Similarity - BM25

The Okapi BM25 Ranking technique is a method of information retrieval used to rank documents based on user input queries; it utilize bag of words-based features. BM25 is not a signle algorithm but is an entire framework of scoring functions that are combined...meaning it's a bit more involved to implement than a basic metric like cosine similarity. The steps in the framework include:
1. Calculating the term frequencies within the documents of the corpus
2. Computing the inverse document frequency of the terms
3. Create BoW features for the corpus documents and query the documents
4. Build a function to compute the BM25 score of given document in relation to a specific document in the corpus
5. Build a function to return the BM25 score of a given document against every other document
6. Build a function to return the pairwise BM25 similarity scores for all documents

Because the code is a bit involved, notes are provided throughout the different functions to explain the processes occurring.

In [ ]:
"""
Data:
-----
.. data:: PARAM_K1 - Free smoothing parameter for BM25.
.. data:: PARAM_B - Free smoothing parameter for BM25.
.. data:: EPSILON - Constant used for negative idf of document in corpus.
"""

import math
from six import iteritems
from six.moves import xrange

PARAM_K1 = 2.5
PARAM_B = 0.85
EPSILON = 0.2

class BM25(object):
    """Implementation of Best Matching 25 ranking function.
    Attributes
    ----------
    corpus_size : int
        Size of corpus (number of documents).
    avgdl : float
        Average length of document in `corpus`.
    corpus : list of list of str
        Corpus of documents.
    f : list of dicts of int
        Dictionary with terms frequencies for each document in `corpus`. Words used as keys and frequencies as values.
    df : dict
        Dictionary with terms frequencies for whole `corpus`. Words used as keys and frequencies as values.
    idf : dict
        Dictionary with inversed terms frequencies for whole `corpus`. Words used as keys and frequencies as values.
    doc_len : list of int
        List of document lengths.
    """

    def __init__(self, corpus):
        """
        Parameters
        ----------
        corpus : list of list of str
            Given corpus.
        """
        self.corpus_size = len(corpus)
        self.avgdl = sum(float(len(x)) for x in corpus) / self.corpus_size
        self.corpus = corpus
        self.f = []
        self.df = {}
        self.idf = {}
        self.doc_len = []
        self.initialize()

    def initialize(self):
        """Calculates frequencies of terms in documents and in corpus. Also computes inverse document frequencies."""
        for document in self.corpus:
            frequencies = {}
            self.doc_len.append(len(document))
            for word in document:
                if word not in frequencies:
                    frequencies[word] = 0
                frequencies[word] += 1
            self.f.append(frequencies)

            for word, freq in iteritems(frequencies):
                if word not in self.df:
                    self.df[word] = 0
                self.df[word] += 1

        for word, freq in iteritems(self.df):
            self.idf[word] = math.log(self.corpus_size - freq + 0.5) - math.log(freq + 0.5)

    def get_score(self, document, index, average_idf):
        """Computes BM25 score of given `document` in relation to item of corpus selected by `index`.
        Parameters
        ----------
        document : list of str
            Document to be scored.
        index : int
            Index of document in corpus selected to score with `document`.
        average_idf : float
            Average idf in corpus.
        Returns
        -------
        float
            BM25 score.
        """
        score = 0
        for word in document:
            if word not in self.f[index]:
                continue
            idf = self.idf[word] if self.idf[word] >= 0 else EPSILON * average_idf
            score += (idf * self.f[index][word] * (PARAM_K1 + 1)
                      / (self.f[index][word] + PARAM_K1 * (1 - PARAM_B + PARAM_B * self.doc_len[index] / self.avgdl)))
        return score

    def get_scores(self, document, average_idf):
        """Computes and returns BM25 scores of given `document` in relation to
        every item in corpus.
        Parameters
        ----------
        document : list of str
            Document to be scored.
        average_idf : float
            Average idf in corpus.
        Returns
        -------
        list of float
            BM25 scores.
        """
        scores = []
        for index in xrange(self.corpus_size):
            score = self.get_score(document, index, average_idf)
            scores.append(score)
        return scores


def get_bm25_weights(corpus):
    """Returns BM25 scores (weights) of documents in corpus.
    Each document has to be weighted with every document in given corpus.
    Parameters
    ----------
    corpus : list of list of str
        Corpus of documents.
    Returns
    -------
    list of list of float
        BM25 scores.
    Examples
    --------
    >>> from gensim.summarization.bm25 import get_bm25_weights
    >>> corpus = [
    ...     ["black", "cat", "white", "cat"],
    ...     ["cat", "outer", "space"],
    ...     ["wag", "dog"]
    ... ]
    >>> result = get_bm25_weights(corpus)
    """
    bm25 = BM25(corpus)
    average_idf = sum(float(val) for val in bm25.idf.values()) / len(bm25.idf)

    weights = []
    for doc in corpus:
        scores = bm25.get_scores(doc, average_idf)
        weights.append(scores)

    return weights

In [ ]:
norm_corpus_tokens = np.array([nltk.word_tokenize(doc) for doc in norm_corpus], dtype='object')  # tokenize words in each document, assign to array of lists
norm_corpus_tokens[:3]

array([list(['enter', 'world', 'pandora', '22nd', 'century', 'paraplegic', 'marine', 'dispatched', 'moon', 'pandora', 'unique', 'mission', 'becomes', 'torn', 'following', 'orders', 'protecting', 'alien', 'civilization']),
       list(['end', 'world', 'adventure', 'begins', 'captain', 'barbossa', 'long', 'believed', 'dead', 'come', 'back', 'life', 'headed', 'edge', 'earth', 'turner', 'elizabeth', 'swann', 'nothing', 'quite', 'seems']),
       list(['plan', 'one', 'escapes', 'cryptic', 'message', 'bonds', 'past', 'sends', 'trail', 'uncover', 'sinister', 'organization', 'battles', 'political', 'forces', 'keep', 'secret', 'service', 'alive', 'bond', 'peels', 'back', 'layers', 'deceit', 'reveal', 'terrible', 'truth', 'behind', 'spectre'])],
      dtype=object)

### 5b) Find Similar Movies

In [ ]:
%%time
wts = get_bm25_weights(norm_corpus_tokens)                                     # get weights of documents

Wall time: 1min 37s


In [ ]:
bm25_wts_df = pd.DataFrame(wts)
bm_25_head = bm25_wts_df.head()
bm_25_head.style.background_gradient(cmap="Blues")

**What is something you notice about the difference of values between cosine distance and bm25 ranking?**

### 6b) Implement Movie Recommender Function

In [ ]:
movie_recommender('Dune', doc_sims=bm25_wts_df)

Based on your interest in Dune I'd Recommend checking out: ['Epic' 'Krull' 'Listening' 'Chronicle' 'Supercapitalist']


**Play around with both movie recommenders on a couple of movie examples, and examine whether the recommendations tend to overlap heavily or whether they tend to recommend different movies. If they aren't overlapping much, do you feel one recommender is better than the other and why?**